# Variables

1. NearestMonth - Front/Second/etc. month at each respective date - starts from 1
2. backAdjustDays - how many days back we need to adjust       # 0 means expired on the day of expiry

In [1]:
import os
import pandas as pd
import numpy as np
from os import walk
import collections

In [2]:
# Path of all files in folder and subfolder - CONTINUE Folder
List_of_files_continue = []
folder_continue = "C:/source/2x4_data/app/data/Barchart/DailyDataDumpCME&NYMEX/dailyContinue/"
folder_names_continue = [os.path.join(folder_continue, name) for name in os.listdir(folder_continue) if os.path.isdir(os.path.join(folder_continue, name))]
folder_names_continue.append(folder_continue)
for fold in folder_names_continue:
    filenames = next(walk(fold), (None, None, []))[2]  # [] if no file
    for file in filenames:
        List_of_files_continue.append(str(fold+"/"+file).replace('//','/'))
List_of_files_continue = [val for val in List_of_files_continue if not val.endswith(".ipynb")] # remove all files end in .ipynb
List_of_files_continue = [val for val in List_of_files_continue if not val.endswith(".pkl")] # remove all files end in .pkl
List_of_files_continue = [val for val in List_of_files_continue if not val.endswith("expiry_df_other_symbols_Continue.csv")]
List_of_files_continue = [val for val in List_of_files_continue if not val.endswith("expiry_df_Continue.csv")]

len(List_of_files_continue)

621

In [3]:
# Path of all files in folder and subfolder - NEAREST Folder
List_of_files_nearest = []
folder_nearest = "C:/source/2x4_data/app/data/Barchart/DailyDataDumpCME&NYMEX/"
folder_names_nearest = [os.path.join(folder_nearest, name) for name in os.listdir(folder_nearest) if os.path.isdir(os.path.join(folder_nearest, name))]
folder_names_nearest.append(folder_nearest)
folder_names_nearest.remove("C:/source/2x4_data/app/data/Barchart/DailyDataDumpCME&NYMEX/dailyContinue")
for fold in folder_names_nearest:
    filenames = next(walk(fold), (None, None, []))[2]  # [] if no file
    for file in filenames:
        List_of_files_nearest.append(str(fold+"/"+file).replace('//','/'))
List_of_files_nearest = [val for val in List_of_files_nearest if not val.endswith(".ipynb")] # remove all files end in .ipynb
List_of_files_nearest = [val for val in List_of_files_nearest if not val.endswith(".pkl")] # remove all files end in .pkl
List_of_files_nearest = [val for val in List_of_files_nearest if not val.endswith("combined_dataframe.csv")]
List_of_files_nearest = [val for val in List_of_files_nearest if not val.endswith("expiry_df.csv")]
List_of_files_nearest = [val for val in List_of_files_nearest if not val.endswith("expiry_df_other_symbols.csv")]

len(List_of_files_nearest)

655

In [4]:
# Matching Nearest & Continue FILES - just remove "_Continue" at the end but before ".csv"
# For each file in Nearest, change the string of the path to make it similar to one in Continue and the check if its exits in Continue

file_paths_dict = {}
for file_nearest in List_of_files_nearest:
    continue_string = file_nearest[file_nearest.rindex('/')+1:]
    continue_string = str(continue_string.replace(".csv","")+"_Continue.csv")
    idx_continue = [i for i, s in enumerate(List_of_files_continue) if continue_string in s]
    file_paths_dict[file_nearest] = List_of_files_continue[idx_continue[0]]

len(file_paths_dict.keys())    
        

655

In [5]:
file_paths_dict['C:/source/2x4_data/app/data/Barchart/DailyDataDumpCME&NYMEX/Archived CSV Files/Australian Dollar(P)_daily_price.csv']

'C:/source/2x4_data/app/data/Barchart/DailyDataDumpCME&NYMEX/dailyContinue/Australian Dollar(P)_daily_price_Continue.csv'

In [6]:
# Get Expiry dataframe from csv
expiry_nearest = pd.read_csv("C:/source/2x4_data/app/data/Barchart/DailyDataDumpCME&NYMEX/expiry_df.csv", index_col=0)
expiry_nearest.head(2)   

symbol exchange contract firstNoticeDate expirationDate  \
MGM22  MGM22     GBLX  _Jun 22       6/13/2022      6/13/2022   
MGH22  MGH22     GBLX  _Mar 22       3/14/2022      3/14/2022   

                                          lastTradingDay  Unnamed: 7  
MGM22  Second business day preceding third Wednesday ...         NaN  
MGH22  Second business day preceding third Wednesday ...         NaN

In [7]:
# Collect all contracts for all commodities in a dictionary and a list of dates
all_dates = []
cmdty_ctrct_dict = {}
cmdty_no_data = []
temp_list = []
cmdty_no_expiry = []
cmdty_ctrct_expiry_dict = collections.defaultdict(dict) # If the amount of nesting you need is fixed, use collections.defaultdict.

for file in file_paths_dict.keys():
    cmdty_name = file[file.rindex('/')+1:].replace('_daily_price.csv','')
    
    try:
        list_nearest_ctrct = pd.read_csv(file)['symbol'].unique().tolist()
        list_nearest_dates = pd.read_csv(file)['tradingDay'].unique().tolist()

    except:
        cmdty_no_data.append(cmdty_name)
        temp_list.append(file_paths_dict[file])

    try:
        list_continue_ctrct = pd.read_csv(file_paths_dict[file],index_col=0)['symbol'].unique().tolist()
        list_continue_dates = pd.read_csv(file_paths_dict[file],index_col=0)['tradingDay'].unique().tolist()

    except:
        cmdty_no_data.append(cmdty_name)
        temp_list.append(file_paths_dict[file])

    cmdty_ctrct_dict[cmdty_name] = set(list_nearest_ctrct + list_continue_ctrct)

    all_dates = all_dates + list_nearest_dates + list_continue_dates

    for ctrcts in cmdty_ctrct_dict[cmdty_name]:
        try:
            cmdty_ctrct_expiry_dict[cmdty_name][ctrcts] = expiry_nearest.loc[ctrcts,'expirationDate'], expiry_nearest.loc[ctrcts,'exchange'], expiry_nearest.loc[ctrcts,'contract'].replace('_','')
        except:
            cmdty_no_expiry.append(ctrcts)

        # To do dict of dicts
	
temp_list =  set(temp_list)
all_dates = set(all_dates)
cmdty_no_data = set(cmdty_no_data)
all_dates = pd.Series(pd.DatetimeIndex(all_dates))
all_dates =  all_dates.sort_values(ascending=False).dt.strftime('%Y-%m-%d').tolist()  


In [8]:

len(cmdty_ctrct_dict.keys()), len(list(cmdty_ctrct_expiry_dict.keys())), len(cmdty_no_expiry)

(618, 561, 6141)

In [9]:
cmdty_ctrct_expiry_dict['AUD_USD Micro']['MGZ20'][2]

'Dec 20'

In [10]:
len(cmdty_no_data), len(file_paths_dict.keys()), len(cmdty_ctrct_dict.keys())

(110, 655, 618)

In [11]:
list(file_paths_dict.keys())[10]

'C:/source/2x4_data/app/data/Barchart/DailyDataDumpCME&NYMEX/Archived CSV Files/Canadian Dollar_daily_price.csv'

Pass a key index such as list(file_paths_dict.keys())[0]

# In the list above look for duplicates and keep the file which is larger.

In [12]:
LS_path = 'C:/source/2x4_data/app/data/Barchart/DailyDataDumpCME&NYMEX/Lumber_daily_price.csv'
file = LS_path
combined = pd.concat([pd.read_csv(file,index_col=0), pd.read_csv(file_paths_dict[file],index_col=0)])
combined.drop_duplicates(inplace=True)
len(combined)


157047

In [13]:
combined

symbol                  timestamp  tradingDay     open     high     low  \
0      LSK22  2022-05-10 00:00:00-05:00  2022-05-10  1008.00  1025.00  1008.0   
1      LSK22  2022-05-09 00:00:00-05:00  2022-05-09  1000.10  1015.00   975.0   
2      LSK22  2022-05-06 00:00:00-05:00  2022-05-06   990.00  1005.00   985.0   
3      LSK22  2022-05-05 00:00:00-05:00  2022-05-05  1010.00  1033.40   993.8   
4      LSK22  2022-05-04 00:00:00-05:00  2022-05-04  1021.60  1025.50   980.0   
...      ...                        ...         ...      ...      ...     ...   
87195  LSK70  1969-10-07 00:00:00-05:00  1969-10-07    81.75    82.00    81.5   
87196  LSK70  1969-10-06 00:00:00-05:00  1969-10-06    81.50    81.50    81.5   
87197  LSK70  1969-10-03 00:00:00-05:00  1969-10-03    81.50    81.50    81.5   
87198  LSK70  1969-10-02 00:00:00-05:00  1969-10-02    81.00    81.25    81.0   
87199  LSK70  1969-10-01 00:00:00-05:00  1969-10-01    80.00    80.75    79.5   

         close  volume  openInterest  Month_Seq  
0      1022.00      53             0          1  
1      1009.00      89           163          1  
2      1000.10     147           237          1  
3      1020.00     131           340          1  
4      1010.00     144           443          1  
...        ...     ...           ...        ...  
87195    82.00       0             0          7  
87196    81.50       0             0          7  
87197    81.50       0             0          7  
87198    81.25       0             0          7  
87199    80.75       0             0          7  

[157047 rows x 10 columns]

In [14]:
cmdty_ctrct_expiry_dict

defaultdict(dict,
            {'3-Month BSBY': {'BRZ21': ('12/31/2021', 'CME', 'Dec 21'),
              'BRU21': ('9/13/2021', 'CME', 'Sep 21'),
              'BRH22': ('3/14/2022', 'CME', 'Mar 22'),
              'BRM22': ('6/13/2022', 'CME', 'Jun 22'),
              'BRZ22': ('12/19/2022', 'CME', 'Dec 22'),
              'BRH23': ('3/13/2023', 'CME', 'Mar 23'),
              'BRU22': ('9/19/2022', 'CME', 'Sep 22'),
              'BRU23': ('9/18/2023', 'CME', 'Sep 23'),
              'BRH24': ('3/18/2024', 'CME', 'Mar 24'),
              'BRM24': ('6/17/2024', 'CME', 'Jun 24'),
              'BRZ23': ('12/18/2023', 'CME', 'Dec 23'),
              'BRH25': ('3/17/2025', 'CME', 'Mar 25'),
              'BRU24': ('9/16/2024', 'CME', 'Sep 24'),
              'BRM23': ('6/19/2023', 'CME', 'Jun 23'),
              'BRZ24': ('12/16/2024', 'CME', 'Dec 24')},
             'Australian Dollar(P)': {'ADH20': ('3/16/2020', 'CME', 'Mar 20'),
              'ADU96': ('9/16/1996', 'CME', 'Sep 96'),
  

In [15]:
one_commodity_expiry = pd.DataFrame(cmdty_ctrct_expiry_dict['Lumber']).T
one_commodity_expiry.columns = ['expiry','exchange','contract']
one_commodity_expiry.expiry = pd.to_datetime(one_commodity_expiry.expiry)
one_commodity_expiry.sort_values(by=['expiry'], ascending= False, inplace=True)
len(one_commodity_expiry)


321

In [16]:
combined

symbol                  timestamp  tradingDay     open     high     low  \
0      LSK22  2022-05-10 00:00:00-05:00  2022-05-10  1008.00  1025.00  1008.0   
1      LSK22  2022-05-09 00:00:00-05:00  2022-05-09  1000.10  1015.00   975.0   
2      LSK22  2022-05-06 00:00:00-05:00  2022-05-06   990.00  1005.00   985.0   
3      LSK22  2022-05-05 00:00:00-05:00  2022-05-05  1010.00  1033.40   993.8   
4      LSK22  2022-05-04 00:00:00-05:00  2022-05-04  1021.60  1025.50   980.0   
...      ...                        ...         ...      ...      ...     ...   
87195  LSK70  1969-10-07 00:00:00-05:00  1969-10-07    81.75    82.00    81.5   
87196  LSK70  1969-10-06 00:00:00-05:00  1969-10-06    81.50    81.50    81.5   
87197  LSK70  1969-10-03 00:00:00-05:00  1969-10-03    81.50    81.50    81.5   
87198  LSK70  1969-10-02 00:00:00-05:00  1969-10-02    81.00    81.25    81.0   
87199  LSK70  1969-10-01 00:00:00-05:00  1969-10-01    80.00    80.75    79.5   

         close  volume  openInterest  Month_Seq  
0      1022.00      53             0          1  
1      1009.00      89           163          1  
2      1000.10     147           237          1  
3      1020.00     131           340          1  
4      1010.00     144           443          1  
...        ...     ...           ...        ...  
87195    82.00       0             0          7  
87196    81.50       0             0          7  
87197    81.50       0             0          7  
87198    81.25       0             0          7  
87199    80.75       0             0          7  

[157047 rows x 10 columns]

In [17]:

ohlcv_option = 'close' # open, high, low, close, volume, openInterest
combined_pivot = pd.pivot_table(combined, values='close', index='tradingDay', columns='symbol').sort_index(ascending=False)
combined_pivot.reindex(one_commodity_expiry.index, axis=1)
len(combined_pivot.columns)
combined_pivot


symbol      LSF00  LSF01  LSF02  LSF03  LSF04  LSF05  LSF06  LSF07  LSF08  \
tradingDay                                                                  
2022-05-10    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2022-05-09    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2022-05-06    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2022-05-05    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2022-05-04    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
...           ...    ...    ...    ...    ...    ...    ...    ...    ...   
1969-10-07    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1969-10-06    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1969-10-03    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1969-10-02    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1969-10-01    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   

symbol      LSF09  ...  LSX91  LSX92  LSX93  LSX94  LSX95  LSX96  LSX97  \
tradingDay         ...                                                    
2022-05-10    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2022-05-09    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2022-05-06    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2022-05-05    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2022-05-04    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
...           ...  ...    ...    ...    ...    ...    ...    ...    ...   
1969-10-07    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1969-10-06    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1969-10-03    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1969-10-02    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1969-10-01    NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   

symbol      LSX98  LSX99  LSZ82  
tradingDay                       
2022-05-10    NaN    NaN    NaN  
2022-05-09    NaN    NaN    NaN  
2022-05-06    NaN    NaN    NaN  
2022-05-05    NaN    NaN    NaN  
2022-05-04    NaN    NaN    NaN  
...           ...    ...    ...  
1969-10-07    NaN    NaN    NaN  
1969-10-06    NaN    NaN    NaN  
1969-10-03    NaN    NaN    NaN  
1969-10-02    NaN    NaN    NaN  
1969-10-01    NaN    NaN    NaN  

[13260 rows x 321 columns]

In [18]:
# same as commodity_pivot but added an extra row at the top for the expiry date
new_combined_pivot = pd.concat([pd.DataFrame(index = one_commodity_expiry.index, data=list(one_commodity_expiry['expiry']),columns=['Expiry']).T,combined_pivot], axis=0)
len(new_combined_pivot)
new_combined_pivot

LSK23                LSH23                LSF23  \
Expiry      2023-05-01 00:00:00  2023-03-15 00:00:00  2023-01-13 00:00:00   
2022-05-10                772.2                796.4                790.0   
2022-05-09                757.4                781.6                775.2   
2022-05-06                784.7                808.9                802.5   
2022-05-05                806.7                830.9                824.5   
...                         ...                  ...                  ...   
1969-10-07                  NaN                  NaN                  NaN   
1969-10-06                  NaN                  NaN                  NaN   
1969-10-03                  NaN                  NaN                  NaN   
1969-10-02                  NaN                  NaN                  NaN   
1969-10-01                  NaN                  NaN                  NaN   

                          LSX22                LSU22                LSN22  \
Expiry      2022-11-15 00:00:00  2022-09-15 00:00:00  2022-07-15 00:00:00   
2022-05-10                765.0                789.5                801.1   
2022-05-09                750.2                784.8                807.7   
2022-05-06                785.6                800.0                827.1   
2022-05-05                795.0                835.6                873.9   
...                         ...                  ...                  ...   
1969-10-07                  NaN                  NaN                  NaN   
1969-10-06                  NaN                  NaN                  NaN   
1969-10-03                  NaN                  NaN                  NaN   
1969-10-02                  NaN                  NaN                  NaN   
1969-10-01                  NaN                  NaN                  NaN   

                          LSK22                LSH22                LSF22  \
Expiry      2022-05-13 00:00:00  2022-03-15 00:00:00  2022-01-14 00:00:00   
2022-05-10               1022.0                  NaN                  NaN   
2022-05-09               1009.0                  NaN                  NaN   
2022-05-06               1000.1                  NaN                  NaN   
2022-05-05               1020.0                  NaN                  NaN   
...                         ...                  ...                  ...   
1969-10-07                  NaN                  NaN                  NaN   
1969-10-06                  NaN                  NaN                  NaN   
1969-10-03                  NaN                  NaN                  NaN   
1969-10-02                  NaN                  NaN                  NaN   
1969-10-01                  NaN                  NaN                  NaN   

                          LSX21  ...                LSU71  \
Expiry      2021-11-15 00:00:00  ...  1971-09-15 00:00:00   
2022-05-10                  NaN  ...                  NaN   
2022-05-09                  NaN  ...                  NaN   
2022-05-06                  NaN  ...                  NaN   
2022-05-05                  NaN  ...                  NaN   
...                         ...  ...                  ...   
1969-10-07                  NaN  ...                  NaN   
1969-10-06                  NaN  ...                  NaN   
1969-10-03                  NaN  ...                  NaN   
1969-10-02                  NaN  ...                  NaN   
1969-10-01                  NaN  ...                  NaN   

                          LSN71                LSK71                LSH71  \
Expiry      1971-07-15 00:00:00  1971-05-14 00:00:00  1971-03-15 00:00:00   
2022-05-10                  NaN                  NaN                  NaN   
2022-05-09                  NaN                  NaN                  NaN   
2022-05-06                  NaN                  NaN                  NaN   
2022-05-05                  NaN                  NaN                  NaN   
...                         ...                  ...    

In [19]:
# Takes a lot of Time - ~ 2minutes for 1 commodity because OF nsmallest(NearestMonth), sort_values is faster ~48 seconds
# Get Front month next at each date
NearestMonth = 1  # starts from month 1 
NearestContract_df = pd.DataFrame()
for dt in new_combined_pivot.index[1:]:

    comp = pd.to_datetime(new_combined_pivot.loc['Expiry'])[dt <= pd.to_datetime(new_combined_pivot.loc['Expiry'])] - pd.to_datetime(dt)
    # active = comp.nsmallest(NearestMonth).index[NearestMonth-1]
    active = comp.sort_values().head(NearestMonth).index[NearestMonth-1]
    temp3 = pd.DataFrame(data=[[dt,active]], columns=['dt','active'])
    NearestContract_df = pd.concat([NearestContract_df,temp3])

In [20]:
NearestContract_df

dt active
0   2022-05-10  LSK22
0   2022-05-09  LSK22
0   2022-05-06  LSK22
0   2022-05-05  LSK22
0   2022-05-04  LSK22
..         ...    ...
0   1969-10-07  LSH70
0   1969-10-06  LSH70
0   1969-10-03  LSH70
0   1969-10-02  LSH70
0   1969-10-01  LSH70

[13260 rows x 2 columns]

In [21]:
NearestContract_df.iloc[39][1], NearestContract_df.iloc[39][0]

('LSH22', '2022-03-15')

In [22]:
new_combined_pivot

LSK23                LSH23                LSF23  \
Expiry      2023-05-01 00:00:00  2023-03-15 00:00:00  2023-01-13 00:00:00   
2022-05-10                772.2                796.4                790.0   
2022-05-09                757.4                781.6                775.2   
2022-05-06                784.7                808.9                802.5   
2022-05-05                806.7                830.9                824.5   
...                         ...                  ...                  ...   
1969-10-07                  NaN                  NaN                  NaN   
1969-10-06                  NaN                  NaN                  NaN   
1969-10-03                  NaN                  NaN                  NaN   
1969-10-02                  NaN                  NaN                  NaN   
1969-10-01                  NaN                  NaN                  NaN   

                          LSX22                LSU22                LSN22  \
Expiry      2022-11-15 00:00:00  2022-09-15 00:00:00  2022-07-15 00:00:00   
2022-05-10                765.0                789.5                801.1   
2022-05-09                750.2                784.8                807.7   
2022-05-06                785.6                800.0                827.1   
2022-05-05                795.0                835.6                873.9   
...                         ...                  ...                  ...   
1969-10-07                  NaN                  NaN                  NaN   
1969-10-06                  NaN                  NaN                  NaN   
1969-10-03                  NaN                  NaN                  NaN   
1969-10-02                  NaN                  NaN                  NaN   
1969-10-01                  NaN                  NaN                  NaN   

                          LSK22                LSH22                LSF22  \
Expiry      2022-05-13 00:00:00  2022-03-15 00:00:00  2022-01-14 00:00:00   
2022-05-10               1022.0                  NaN                  NaN   
2022-05-09               1009.0                  NaN                  NaN   
2022-05-06               1000.1                  NaN                  NaN   
2022-05-05               1020.0                  NaN                  NaN   
...                         ...                  ...                  ...   
1969-10-07                  NaN                  NaN                  NaN   
1969-10-06                  NaN                  NaN                  NaN   
1969-10-03                  NaN                  NaN                  NaN   
1969-10-02                  NaN                  NaN                  NaN   
1969-10-01                  NaN                  NaN                  NaN   

                          LSX21  ...                LSU71  \
Expiry      2021-11-15 00:00:00  ...  1971-09-15 00:00:00   
2022-05-10                  NaN  ...                  NaN   
2022-05-09                  NaN  ...                  NaN   
2022-05-06                  NaN  ...                  NaN   
2022-05-05                  NaN  ...                  NaN   
...                         ...  ...                  ...   
1969-10-07                  NaN  ...                  NaN   
1969-10-06                  NaN  ...                  NaN   
1969-10-03                  NaN  ...                  NaN   
1969-10-02                  NaN  ...                  NaN   
1969-10-01                  NaN  ...                  NaN   

                          LSN71                LSK71                LSH71  \
Expiry      1971-07-15 00:00:00  1971-05-14 00:00:00  1971-03-15 00:00:00   
2022-05-10                  NaN                  NaN                  NaN   
2022-05-09                  NaN                  NaN                  NaN   
2022-05-06                  NaN                  NaN                  NaN   
2022-05-05                  NaN                  NaN                  NaN   
...                         ...                  ...    

In [23]:
new_combined_pivot.loc[NearestContract_df.iloc[39][0],NearestContract_df.iloc[39][1]]

1420.0

In [24]:
some_dt = '2022-03-15'
NearestContract_df[NearestContract_df['dt'] == some_dt]

dt active
0  2022-03-15  LSH22

In [25]:
NearestContract_df['close'] = np.nan
NearestContract_df.reset_index(inplace = True)
NearestContract_df.drop('index', axis=1,inplace = True)
for i in range(len(NearestContract_df)):
    NearestContract_df.loc[i, 'close'] = new_combined_pivot.loc[NearestContract_df.iloc[i][0],NearestContract_df.iloc[i][1]]

    # New code
#     NearestContract_df.loc[i, 'open'] = new_combined_pivot.loc[NearestContract_df.iloc[i][0],NearestContract_df.iloc[i][1]]
# open, high, low, close, volume, openInterest

NearestContract_df

dt active   close
0      2022-05-10  LSK22  1022.0
1      2022-05-09  LSK22  1009.0
2      2022-05-06  LSK22  1000.1
3      2022-05-05  LSK22  1020.0
4      2022-05-04  LSK22  1010.0
...           ...    ...     ...
13255  1969-10-07  LSH70    79.0
13256  1969-10-06  LSH70    80.0
13257  1969-10-03  LSH70    80.0
13258  1969-10-02  LSH70    80.5
13259  1969-10-01  LSH70    80.0

[13260 rows x 3 columns]

In [26]:
NearestContract_df[38:]

dt active   close
38     2022-03-16  LSK22  1150.0
39     2022-03-15  LSH22  1420.0
40     2022-03-14  LSH22  1410.0
41     2022-03-11  LSH22  1410.0
42     2022-03-10  LSH22  1348.5
...           ...    ...     ...
13255  1969-10-07  LSH70    79.0
13256  1969-10-06  LSH70    80.0
13257  1969-10-03  LSH70    80.0
13258  1969-10-02  LSH70    80.5
13259  1969-10-01  LSH70    80.0

[13222 rows x 3 columns]

In [27]:
backAdjustDays = 2       # 0 means expired on the day of expiry
NearestContractShifted_df = NearestContract_df.copy(deep=True)
shifted_contracts = pd.Series(NearestContractShifted_df.active[0:backAdjustDays+1].values)
NearestContractShifted_df.active = NearestContractShifted_df.active.shift(periods=(backAdjustDays+1))
NearestContractShifted_df.active.iloc[0:backAdjustDays+1] = shifted_contracts
NearestContractShifted_df.active.reset_index(drop=True, inplace=True)

for i in range(len(NearestContractShifted_df)):
    NearestContractShifted_df.loc[i, 'close'] = new_combined_pivot.loc[NearestContractShifted_df.iloc[i][0],NearestContractShifted_df.iloc[i][1]]

NearestContractShifted_df

C:\Users\Fanjum_cwp\AppData\Local\Temp\2\ipykernel_23084\1244273054.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  NearestContractShifted_df.active.iloc[0:backAdjustDays+1] = shifted_contracts


dt active   close
0      2022-05-10  LSK22  1022.0
1      2022-05-09  LSK22  1009.0
2      2022-05-06  LSK22  1000.1
3      2022-05-05  LSK22  1020.0
4      2022-05-04  LSK22  1010.0
...           ...    ...     ...
13255  1969-10-07  LSH70    79.0
13256  1969-10-06  LSH70    80.0
13257  1969-10-03  LSH70    80.0
13258  1969-10-02  LSH70    80.5
13259  1969-10-01  LSH70    80.0

[13260 rows x 3 columns]

In [28]:
NearestContractShifted_df[38:]

dt active   close
38     2022-03-16  LSK22  1150.0
39     2022-03-15  LSK22  1160.4
40     2022-03-14  LSK22  1103.4
41     2022-03-11  LSK22  1159.2
42     2022-03-10  LSH22  1348.5
...           ...    ...     ...
13255  1969-10-07  LSH70    79.0
13256  1969-10-06  LSH70    80.0
13257  1969-10-03  LSH70    80.0
13258  1969-10-02  LSH70    80.5
13259  1969-10-01  LSH70    80.0

[13222 rows x 3 columns]

In [29]:
NearestContractShifted_df[NearestContractShifted_df.close.isna()][:5]

dt active  close
6363   1997-01-31  LSH97    NaN
10106  1982-04-07  LSZ82    NaN
10107  1982-04-06  LSZ82    NaN
10108  1982-04-05  LSZ82    NaN
10109  1982-04-02  LSZ82    NaN

In [30]:
NearestContract_df[(NearestContract_df.dt == '1982-04-02') & (NearestContract_df.active == 'LSZ82')]

dt active  close
10109  1982-04-02  LSZ82    NaN

In [31]:
NearestContractShifted_df[38:41]

dt active   close
38  2022-03-16  LSK22  1150.0
39  2022-03-15  LSK22  1160.4
40  2022-03-14  LSK22  1103.4

In [32]:
NearestContract_df[38:41]

dt active   close
38  2022-03-16  LSK22  1150.0
39  2022-03-15  LSH22  1420.0
40  2022-03-14  LSH22  1410.0

In [33]:
len(NearestContract_df), len(NearestContractShifted_df)

(13260, 13260)

In [34]:

NearestContract_df.index = NearestContract_df.dt
NearestContract_df.drop('dt', axis=1,inplace = True)

NearestContractShifted_df.index = NearestContractShifted_df.dt
NearestContractShifted_df.drop('dt', axis=1,inplace = True)

ComparisonNearestContractdf=NearestContract_df.compare(NearestContractShifted_df)
ComparisonNearestContractdf

active           close        
             self  other     self   other
dt                                       
2022-03-15  LSH22  LSK22  1420.00  1160.4
2022-03-14  LSH22  LSK22  1410.00  1103.4
2022-03-11  LSH22  LSK22  1410.00  1159.2
2022-01-14  LSF22  LSH22  1237.10  1308.7
2022-01-13  LSF22  LSH22  1229.10  1329.0
...           ...    ...      ...     ...
1970-05-14  LSK70  LSN70    73.50    77.5
1970-05-13  LSK70  LSN70    73.25    78.5
1970-03-13  LSH70  LSK70    70.50    77.5
1970-03-12  LSH70  LSK70    75.50    79.0
1970-03-11  LSH70  LSK70    75.50    79.5

[942 rows x 4 columns]

In [35]:

ComparisonNearestContractdf['Diff'] = ComparisonNearestContractdf.loc[:,('close','other')].sub(ComparisonNearestContractdf.loc[:,('close','self')], axis = 0)
ComparisonNearestContractdf['Prod'] = ComparisonNearestContractdf.loc[:,('close','other')].div(ComparisonNearestContractdf.loc[:,('close','self')])
ComparisonNearestContractdf


active           close            Diff      Prod
             self  other     self   other                  
dt                                                         
2022-03-15  LSH22  LSK22  1420.00  1160.4 -259.60  0.817183
2022-03-14  LSH22  LSK22  1410.00  1103.4 -306.60  0.782553
2022-03-11  LSH22  LSK22  1410.00  1159.2 -250.80  0.822128
2022-01-14  LSF22  LSH22  1237.10  1308.7   71.60  1.057877
2022-01-13  LSF22  LSH22  1229.10  1329.0   99.90  1.081279
...           ...    ...      ...     ...     ...       ...
1970-05-14  LSK70  LSN70    73.50    77.5    4.00  1.054422
1970-05-13  LSK70  LSN70    73.25    78.5    5.25  1.071672
1970-03-13  LSH70  LSK70    70.50    77.5    7.00  1.099291
1970-03-12  LSH70  LSK70    75.50    79.0    3.50  1.046358
1970-03-11  LSH70  LSK70    75.50    79.5    4.00  1.052980

[942 rows x 6 columns]

In [39]:
ComparisonNearestContractdf['Diff']

dt
2022-03-15   -259.60
2022-03-14   -306.60
2022-03-11   -250.80
2022-01-14     71.60
2022-01-13     99.90
               ...  
1970-05-14      4.00
1970-05-13      5.25
1970-03-13      7.00
1970-03-12      3.50
1970-03-11      4.00
Name: Diff, Length: 942, dtype: float64

In [36]:
# diff_df = pd.DataFrame(index = NearestContract_df.index, data = ComparisonNearestContractdf['Diff'])
# # diff_df.reset_levels(0, inplace=True)
# diff_df.fillna(method='ffill',inplace = True)
# diff_df.fillna(0,inplace = True)
# diff_df

# Cumulative Adjustment - Choice Used 'Substraction'

In [37]:
# THIS IS THE ORIGINAL CODE WHICH WORKS - IT DOESN'T HAVE WEIGHTS AND THIS IS FOR SUBSTRACTION METHOD

# default weights
# weights = [1/(backAdjustDays+1)]*(backAdjustDays+1)
# # weights = [0.20,0.35,0.45]


# option = 'sub' # OR 'prod'
# if(option == 'sub'):
#     column_name = 'Diff'
#     cumulative_df = pd.DataFrame(index = ComparisonNearestContractdf.index, data = ComparisonNearestContractdf[column_name])
#     cumulative_df.reset_index(inplace=True)
#     pivot_backAdjustDays_idx = [x for x in cumulative_df.index if (x % (backAdjustDays+1)) == backAdjustDays]

#     # following 2 lines make sure that only the value correspoding to (expiry date - backAdjustDays) is taken back for adjustment - see excels
#     cumulative_df['flag'] = [1 if x in pivot_backAdjustDays_idx else 0 for x in cumulative_df.index]
#     cumulative_df['backAdjDay_effect'] =  (cumulative_df[column_name]*cumulative_df['flag']).cumsum()

#     # The following 2 lines takes care of impact b4 backAdjustDays
#     cumulative_df['flag'] = 1 - cumulative_df['flag']
#     cumulative_df['Total_effect'] = (cumulative_df[column_name]*cumulative_df['flag']) + cumulative_df['backAdjDay_effect']

#     cumulative_df.index  = cumulative_df.dt
#     cumulative_df.drop('dt', axis=1,inplace = True)

#     final_df = pd.DataFrame(index = NearestContract_df.index, data = cumulative_df['Total_effect'] )
#     final_df.fillna(method='ffill',inplace = True)
#     final_df.fillna(0,inplace = True)
#     final_df['close'] = NearestContract_df['close'].values
#     final_df['Adjusted'] = final_df['close'] + final_df['Total_effect']
    


In [50]:
# (cumulative_df.index == ComparisonNearestContractdf.index).all()
# cumulative_df.index
ComparisonNearestContractdf.loc['2022-03-15','Diff']

   -259.6
Name: 2022-03-15, dtype: object

In [52]:


# default weights
weights = [1/(backAdjustDays+1)]*(backAdjustDays+1)
weights = [0.20,0.35,0.45]

# Note that for all days from expiry to backAdjustDays, the multiplier remains the same. It also remains same from backadjustDays till next expiry

column_name = 'Diff'
cumulative_df = pd.DataFrame(index = ComparisonNearestContractdf.index, data = ComparisonNearestContractdf[column_name])
cumulative_df.reset_index(inplace=True)

# Put weighted average for all days from expiry till backAdjustDays
cumulative_df['wt_avg'] = cumulative_df[column_name].groupby(cumulative_df.index//(backAdjustDays+1)).apply(lambda x: np.multiply(x,weights)).groupby(cumulative_df.index//(backAdjustDays+1)).transform('sum')
cumulative_df['Cum_effect'] = cumulative_df['wt_avg']

# flag == 1 represents (expiry + backAdjustDays)
pivot_backAdjustDays_idx = [x for x in cumulative_df.index if (x % (backAdjustDays+1)) == backAdjustDays]

cumulative_df['flag'] = [1 if x in pivot_backAdjustDays_idx else 0 for x in cumulative_df.index]

cumulative_df.loc[cumulative_df['flag'] == 0, 'Cum_effect'] = 0 # Put 0 for all days before backAdjustDays so as to make cumsum work
cumulative_df['Cum_effect'] = cumulative_df['Cum_effect'].cumsum()

# Once we have forward filled the cumulative effect, we can take the cumulative effect for days before backAdjustDays
# cumulative_df.loc[cumulative_df['flag'] == 0, 'Total_effect'] = cumulative_df['Cum_effect'] + cumulative_df['wt_avg']
cumulative_df.loc[cumulative_df['flag'] == 1, 'Total_effect'] = cumulative_df['Cum_effect']

# Once we have forward filled the cumulative effect, we can take the actual difference for days before backAdjustDays
for idx in cumulative_df.index:
    cumulative_df.loc[cumulative_df['flag'] == 0, 'Total_effect']  = ComparisonNearestContractdf.loc[idx,'Diff']


cumulative_df.index  = cumulative_df.dt
cumulative_df.drop('dt', axis=1,inplace = True)

final_df = pd.DataFrame(index = NearestContract_df.index, data = cumulative_df['Total_effect'] )
final_df.fillna(method='ffill',inplace = True)
final_df.fillna(0,inplace = True)
final_df['close'] = NearestContract_df['close'].values
final_df['Adjusted'] = final_df['close'] + final_df['Total_effect']

final_df



KeyError: 0

In [ ]:
# cumulative_df

In [ ]:
# cumulative_df
final_df

In [ ]:
final_df[38:]

In [ ]:
final_df[78:]

In [ ]:
final_df[120:]

# PRODUCT Method of Panama

In [ ]:
ComparisonNearestContractdf['Prod']

In [ ]:
# default weights
weights = [1/(backAdjustDays+1)]*(backAdjustDays+1)
weights = [0.20,0.35,0.45]


# Note that for all days from expiry to backAdjustDays, the multiplier remains the same. It also remains same from backadjustDays till next expiry
column_name = 'Prod'
cumulative_df = pd.DataFrame(index = ComparisonNearestContractdf.index, data = ComparisonNearestContractdf[column_name])
cumulative_df.reset_index(inplace=True)

# Put weighted average for all days from expiry till backAdjustDays
cumulative_df['wt_avg'] = cumulative_df[column_name].groupby(cumulative_df.index//(backAdjustDays+1)).apply(lambda x: np.multiply(x,weights)).groupby(cumulative_df.index//(backAdjustDays+1)).transform('sum')
cumulative_df['Cum_effect'] = cumulative_df['wt_avg']

# flag == 1 represents (expiry + backAdjustDays)
pivot_backAdjustDays_idx = [x for x in cumulative_df.index if (x % (backAdjustDays+1)) == backAdjustDays]
cumulative_df['flag'] = [1 if x in pivot_backAdjustDays_idx else 0 for x in cumulative_df.index]

cumulative_df.loc[cumulative_df['flag'] == 0, 'Cum_effect'] = 1 # Put 1 for all days before backAdjustDays so as to make cumprod work
cumulative_df['Cum_effect'] = cumulative_df['Cum_effect'].cumprod()

# Once we have forward filled the cumulative effect, we can take the cumulative effect for days before backAdjustDays
cumulative_df.loc[cumulative_df['flag'] == 0, 'Total_effect'] = cumulative_df['Cum_effect'] * cumulative_df['wt_avg']
cumulative_df.loc[cumulative_df['flag'] == 1, 'Total_effect'] = cumulative_df['Cum_effect']

cumulative_df.index  = cumulative_df.dt
cumulative_df.drop('dt', axis=1,inplace = True)

final_df = pd.DataFrame(index = NearestContract_df.index, data = cumulative_df['Total_effect'] )
final_df.fillna(method='ffill',inplace = True)
final_df.fillna(1,inplace = True)
final_df['close'] = NearestContract_df['close'].values
final_df['Adjusted'] = final_df['close'] * final_df['Total_effect']

final_df


In [ ]:
final_df[38:]

In [ ]:
final_df[78:]

In [ ]:
final_df[4978:]

In [ ]:
# final_df.to_csv('C:/source/2x4_data/app/data/Barchart/final_df_2dayb4_copy.csv')

In [ ]:
final_df.loc['2001-04-30']

In [ ]:
final_df[78:]

# Joining 2 methods

## Absolute - or difference

In [ ]:

if(method== 'absolute'):

# default weights
weights = [1/(backAdjustDays+1)]*(backAdjustDays+1)
# weights = [0.20,0.35,0.45]


# Note that for all days from expiry to backAdjustDays, the multiplier remains the same. It also remains same from backadjustDays till next expiry

column_name = 'Diff'
cumulative_df = pd.DataFrame(index = ComparisonNearestContractdf.index, data = ComparisonNearestContractdf[column_name])
cumulative_df.reset_index(inplace=True)

# Put weighted average for all days from expiry till backAdjustDays
cumulative_df['wt_avg'] = cumulative_df[column_name].groupby(cumulative_df.index//(backAdjustDays+1)).apply(lambda x: np.multiply(x,weights)).groupby(cumulative_df.index//(backAdjustDays+1)).transform('sum')
cumulative_df['Cum_effect'] = cumulative_df['wt_avg']

# flag == 1 represents (expiry + backAdjustDays)
pivot_backAdjustDays_idx = [x for x in cumulative_df.index if (x % (backAdjustDays+1)) == backAdjustDays]

cumulative_df['flag'] = [1 if x in pivot_backAdjustDays_idx else 0 for x in cumulative_df.index]


cumulative_df.loc[cumulative_df['flag'] == 0, 'Cum_effect'] = 0 # Put 0 for all days before backAdjustDays so as to make cumsum work
cumulative_df['Cum_effect'] = cumulative_df['Cum_effect'].cumsum()

# Once we have forward filled the cumulative effect, we can take the cumulative effect for days before backAdjustDays
cumulative_df.loc[cumulative_df['flag'] == 0, 'Total_effect'] = cumulative_df['Cum_effect'] + cumulative_df['wt_avg']
cumulative_df.loc[cumulative_df['flag'] == 1, 'Total_effect'] = cumulative_df['Cum_effect']

cumulative_df.index  = cumulative_df.dt
cumulative_df.drop('dt', axis=1,inplace = True)

final_df = pd.DataFrame(index = NearestContract_df.index, data = cumulative_df['Total_effect'] )
final_df.fillna(method='ffill',inplace = True)
final_df.fillna(0,inplace = True)
final_df['close'] = NearestContract_df['close'].values
final_df['Adjusted'] = final_df['close'] + final_df['Total_effect']

final_df



## Relative or product method

In [ ]:


# Note that for all days from expiry to backAdjustDays, the multiplier remains the same. It also remains same from backadjustDays till next expiry

column_name = 'Prod'
cumulative_df = pd.DataFrame(index = ComparisonNearestContractdf.index, data = ComparisonNearestContractdf[column_name])
cumulative_df.reset_index(inplace=True)

# Put weighted average for all days from expiry till backAdjustDays
cumulative_df['wt_avg'] = cumulative_df[column_name].groupby(cumulative_df.index//(backAdjustDays+1)).apply(lambda x: np.multiply(x,weights)).groupby(cumulative_df.index//(backAdjustDays+1)).transform('sum')
cumulative_df['Cum_effect'] = cumulative_df['wt_avg']

# flag == 1 represents (expiry + backAdjustDays)
pivot_backAdjustDays_idx = [x for x in cumulative_df.index if (x % (backAdjustDays+1)) == backAdjustDays]
cumulative_df['flag'] = [1 if x in pivot_backAdjustDays_idx else 0 for x in cumulative_df.index]

cumulative_df.loc[cumulative_df['flag'] == 0, 'Cum_effect'] = 1 # Put 1 for all days before backAdjustDays so as to make cumprod work
cumulative_df['Cum_effect'] = cumulative_df['Cum_effect'].cumprod()

# Once we have forward filled the cumulative effect, we can take the cumulative effect for days before backAdjustDays
cumulative_df.loc[cumulative_df['flag'] == 0, 'Total_effect'] = cumulative_df['Cum_effect'] * cumulative_df['wt_avg']
cumulative_df.loc[cumulative_df['flag'] == 1, 'Total_effect'] = cumulative_df['Cum_effect']

cumulative_df.index  = cumulative_df.dt
cumulative_df.drop('dt', axis=1,inplace = True)

final_df = pd.DataFrame(index = NearestContract_df.index, data = cumulative_df['Total_effect'] )
final_df.fillna(method='ffill',inplace = True)
final_df.fillna(1,inplace = True)
final_df['close'] = NearestContract_df['close'].values
final_df['Adjusted'] = final_df['close'] * final_df['Total_effect']

final_df


In [ ]:
# pd.MultiIndex.from_frame(ComparisonNearestContractdf)

ComparisonNearestContractdf.columns.get_level_values(0), ComparisonNearestContractdf.columns.get_level_values(1)

In [ ]:
ComparisonNearestContractdf.iloc[:, ComparisonNearestContractdf.columns.get_level_values(1)=='self']

In [ ]:
# Check if any of the expiries are less than 2 std dev away from the mean of the date difference between 2 consecutive expiry months

def zscore(s):
    return (s - np.mean(s)) / np.std(s)

# Check if difference in dates is more or less similar - left starting 2 dates - becasue one will be NaN and other is current day so wil be less
expiry_month_diff = pd.to_datetime(new_combined_pivot.loc['Expiry']).diff().dt.days[2:].values
pd.Series(expiry_month_diff)[zscore(pd.Series(expiry_month_diff)).abs().gt(2)]

In [ ]:
columns = ['Cmdty','M1','M2','M3','M4','M5','M6','M7','M8','M9','M10','M11','M12']
one_cmdty_df = pd.DataFrame(columns=columns, index=all_dates)
cmdty_calender_mnths = pd.DataFrame(columns=columns)

In [ ]:
cmdty_calender_mnths

In [ ]:
# cmdty_ctrct_dict['AUD_USD Micro']
cmdty_ctrct_expiry_dict['AUD_USD Micro']['MGM21']

In [ ]:
cmdty_date_df = pd.DataFrame(columns=['Dates'])
cmdty_date_df.loc['2','Dates'] = 1
# cmdty_date_df

In [ ]:
import datetime
def date_less_than(date, ctrct_expiry):
    return date <= ctrct_expiry 

# def date_greater_than(end, current):
#     return current <= end

stick together continue & nearest contracts